In [75]:
import random
import os
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from tqdm import trange
from torch.autograd import Variable
import numpy as np
from sklearn.metrics import f1_score
from seqeval.metrics import f1_score as f1_score_seqeval
from seqeval.metrics import classification_report
from seqeval.scheme import IOB1

In [76]:
import gensim.downloader
word2vec_goog1e_news: gensim.models.keyedvectors.KeyedVectors = gensim.downloader.load('word2vec-google-news-300')
word2vec_goog1e_news.add_vector("<pad>", np.zeros(300))
pad_index = word2vec_goog1e_news.key_to_index["<pad>"]
embedding_weights = torch.FloatTensor(word2vec_goog1e_news.vectors)
vocab = word2vec_goog1e_news.key_to_index
# UNK is already inside word2vec_google_news
# weights = torch.FloatTensor(word2vec_goog1e_news.vectors)
# embedding = nn.Embedding.from_pretrained(weights)
# WORD = 'UNK'
# WORDID = word2vec_goog1e_news.key_to_index[WORD]
# print(f"WORDID: {WORDID}")

c:\Users\jerem\OneDrive\Documents\NLP_Assignment\SC4002_NLP\venv\lib\site-packages\gensim\models\keyedvectors.py:551: UserWarning: Adding single vectors to a KeyedVectors which grows by one each time can be costly. Consider adding in batches or preallocating to the required size.
  warnings.warn(


In [77]:
def read_conll_file(file_path):
    sentences = []
    sentence = []
    tags = []
    tag = []
    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            line = line.strip()
            if len(line) == 0:  # Empty line indicates the end of a sentence
                if sentence:
                    sentences.append(sentence)
                    tags.append(tag)
                sentence = []
                tag = []
            else:
                parts = line.split()
                word = parts[0]
                if word == '-DOCSTART-':
                    continue
                ner_tag = parts[-1]
                sentence.append(word)
                tag.append(ner_tag)
        if sentence:
            sentences.append(sentence)
            tags.append(tag)
    return sentences, tags

In [78]:
train_data, train_tags = read_conll_file('CoNLL2003_dataset/eng.train')
val_data, val_tags = read_conll_file('CoNLL2003_dataset/eng.testa')
test_data, test_tags = read_conll_file('CoNLL2003_dataset/eng.testb')

In [79]:
from itertools import chain

def get_unique_words(allSentences):
    uniqueWords = [] 
    flatten_sentences = list(chain(*allSentences))
    for i in flatten_sentences:
        if not i in uniqueWords:
            uniqueWords.append(i);
    uniqueWords.append('<pad>')
    uniqueWords.append('UNK')
    return uniqueWords

def get_unique_tags(allTags):
    uniqueWords = []
    flatten_sentences = list(chain(*allTags))
    for i in flatten_sentences:
        if not i in uniqueWords:
            uniqueWords.append(i);
    return uniqueWords

In [80]:
unique_words = get_unique_words(train_data+val_data) # test_data not included
unique_tags = get_unique_tags(train_tags+val_tags+test_tags)

In [81]:
tag_map = {}
for index, tag in enumerate(unique_tags):
    tag_map[tag] = index
tag_map

{'I-ORG': 0,
 'O': 1,
 'I-MISC': 2,
 'I-PER': 3,
 'I-LOC': 4,
 'B-LOC': 5,
 'B-MISC': 6,
 'B-ORG': 7}

In [82]:
def indexify(data, tag):
    setences = []
    labels = []
    for sentence in data:
        s = [vocab[token] if token in vocab
            else vocab['UNK']
            for token in sentence]
        setences.append(s)

    for sentence in tag:
        l = [tag_map[label] for label in sentence]
        labels.append(l)

    return setences, labels

train_sentences = []
train_labels = []

val_sentences = []
val_labels = []

test_sentences = []
test_labels = []

train_sentences, train_labels = indexify(train_data, train_tags)
val_sentences, val_labels = indexify(val_data, val_tags)
test_sentences, test_labels = indexify(test_data, test_tags)

In [83]:
# print(f"train_sentences: \n {train_sentences}")
# print(f"train_labels: \n {train_labels}")

In [84]:
def data_iterator(sentences, labels, total_size: int, batch_size: int, shuffle: bool=False):
    # make a list that decides the order in which we go over the data- this avoids explicit shuffling of data
    order = list(range(total_size))
    if shuffle:
        random.seed(230)
        random.shuffle(order)

    # one pass over data
    for i in range((total_size+1)//batch_size):
        # fetch sentences and tags
        batch_sentences = [sentences[idx] for idx in order[i*batch_size:(i+1)*batch_size]]
        batch_tags = [labels[idx] for idx in order[i*batch_size:(i+1)*batch_size]]

        # compute length of longest sentence in batch
        batch_max_len = max([len(s) for s in batch_sentences])

        # prepare a numpy array with the data, initialising the data with pad_ind and all labels with -1
        # initialising labels to -1 differentiates tokens with tags from PADding tokens
        batch_data = vocab['<pad>']*np.ones((len(batch_sentences), batch_max_len))
        batch_labels = -1*np.ones((len(batch_sentences), batch_max_len))

        # copy the data to the numpy array
        for j in range(len(batch_sentences)):
            cur_len = len(batch_sentences[j])
            batch_data[j][:cur_len] = batch_sentences[j]
            batch_labels[j][:cur_len] = batch_tags[j]

        # since all data are indices, we convert them to torch LongTensors
        batch_data, batch_labels = torch.LongTensor(batch_data), torch.LongTensor(batch_labels)

        # shift tensors to GPU if available
        # if params.cuda:
        #     batch_data, batch_labels = batch_data.cuda(), batch_labels.cuda()

        # convert them to Variables to record operations in the computational graph
        batch_data, batch_labels = Variable(batch_data), Variable(batch_labels)

        yield batch_data, batch_labels, batch_sentences

In [85]:
class Net(nn.Module):
    """
    This is the standard way to define your own network in PyTorch. You typically choose the components
    (e.g. LSTMs, linear layers etc.) of your network in the __init__ function. You then apply these layers
    on the input step-by-step in the forward function. You can use torch.nn.functional to apply functions
    such as F.relu, F.sigmoid, F.softmax. Be careful to ensure your dimensions are correct after each step.

    You are encouraged to have a look at the network in pytorch/vision/model/net.py to get a better sense of how
    you can go about defining your own network.

    The documentation for all the various components available to you is here: http://pytorch.org/docs/master/nn.html
    """

    def __init__(self, embedding_weights, embedding_dim, lstm_hidden_dim, number_of_tags):
        """
        We define an recurrent network that predicts the NER tags for each token in the sentence. The components
        required are:

        - an embedding layer: this layer maps each index in range(params.vocab_size) to a params.embedding_dim vector
        - lstm: applying the LSTM on the sequential input returns an output for each token in the sentence
        - fc: a fully connected layer that converts the LSTM output for each token to a distribution over NER tags

        Args:
            params: (Params) contains vocab_size, embedding_dim, lstm_hidden_dim
        """
        super(Net, self).__init__()

        # the embedding takes as input the vocab_size and the embedding_dim
        # self.embedding = nn.Embedding(vocab_size, embedding_dim)
        self.embedding = nn.Embedding.from_pretrained(embedding_weights, padding_idx=pad_index)

        # the LSTM takes as input the size of its input (embedding_dim), its hidden size
        # for more details on how to use it, check out the documentation
        self.lstm = nn.LSTM(embedding_dim,
                            lstm_hidden_dim, batch_first=True)

        # the fully connected layer transforms the output to give the final output layer
        self.fc = nn.Linear(lstm_hidden_dim, number_of_tags)

    def forward(self, s):
        """
        This function defines how we use the components of our network to operate on an input batch.

        Args:
            s: (Variable) contains a batch of sentences, of dimension batch_size x seq_len, where seq_len is
               the length of the longest sentence in the batch. For sentences shorter than seq_len, the remaining
               tokens are PADding tokens. Each row is a sentence with each element corresponding to the index of
               the token in the vocab.

        Returns:
            out: (Variable) dimension batch_size*seq_len x num_tags with the log probabilities of tokens for each token
                 of each sentence.

        Note: the dimensions after each step are provided
        """
        #                                -> batch_size x seq_len
        # apply the embedding layer that maps each token to its embedding
        # dim: batch_size x seq_len x embedding_dim
        s = self.embedding(s)

        # run the LSTM along the sentences of length seq_len
        # dim: batch_size x seq_len x lstm_hidden_dim
        s, _ = self.lstm(s)

        # make the Variable contiguous in memory (a PyTorch artefact)
        s = s.contiguous()

        # reshape the Variable so that each row contains one token
        # dim: batch_size*seq_len x lstm_hidden_dim
        s = s.view(-1, s.shape[2])

        # apply the fully connected layer and obtain the output (before softmax) for each token
        s = self.fc(s)                   # dim: batch_size*seq_len x num_tags

        # apply log softmax on each token's output (this is recommended over applying softmax
        # since it is numerically more stable)
        return F.log_softmax(s, dim=1)   # dim: batch_size*seq_len x num_tags

In [86]:
def loss_fn(outputs, labels):
    """
    Compute the cross entropy loss given outputs from the model and labels for all tokens. Exclude loss terms
    for PADding tokens.

    Args:
        outputs: (Variable) dimension batch_size*seq_len x num_tags - log softmax output of the model
        labels: (Variable) dimension batch_size x seq_len where each element is either a label in [0, 1, ... num_tag-1],
                or -1 in case it is a PADding token.

    Returns:
        loss: (Variable) cross entropy loss for all tokens in the batch

    Note: you may use a standard loss function from http://pytorch.org/docs/master/nn.html#loss-functions. This example
          demonstrates how you can easily define a custom loss function.
    """

    # reshape labels to give a flat vector of length batch_size*seq_len
    labels = labels.view(-1)

    # since PADding tokens have label -1, we can generate a mask to exclude the loss from those terms
    mask = (labels >= 0).float()

    # indexing with negative values is not supported. Since PADded tokens have label -1, we convert them to a positive
    # number. This does not affect training, since we ignore the PADded tokens with the mask.
    labels = labels % outputs.shape[1]

    num_tokens = int(torch.sum(mask))

    # compute cross entropy loss for all tokens (except PADding tokens), by multiplying with mask.
    return -torch.sum(outputs[range(outputs.shape[0]), labels]*mask)/num_tokens

In [87]:
class RunningAverage:
    """A simple class that maintains the running average of a quantity

    Example:
    ```
    loss_avg = RunningAverage()
    loss_avg.update(2)
    loss_avg.update(4)
    loss_avg() = 3
    ```
    """

    def __init__(self):
        self.steps = 0
        self.total = 0

    def update(self, val):
        self.total += val
        self.steps += 1

    def __call__(self):
        return self.total / float(self.steps)

In [88]:
def train(model, optimizer, loss_fn, data_iterator, metrics, num_steps):
    """Train the model on `num_steps` batches

    Args:
        model: (torch.nn.Module) the neural network
        optimizer: (torch.optim) optimizer for parameters of model
        loss_fn: a function that takes batch_output and batch_labels and computes the loss for the batch
        data_iterator: (generator) a generator that generates batches of data and labels
        metrics: (dict) a dictionary of functions that compute a metric using the output and labels of each batch
        params: (Params) hyperparameters
        num_steps: (int) number of batches to train on, each of size params.batch_size
    """

    # set model to training mode
    model.train()

    # summary for current training loop and a running average object for loss
    summ = []
    loss_avg = RunningAverage()

    # Use tqdm for progress bar
    t = trange(num_steps)
    for i in t:
        # fetch the next training batch
        train_batch, labels_batch, _ = next(data_iterator)

        # compute model output and loss
        output_batch = model(train_batch)
        loss = loss_fn(output_batch, labels_batch)

        # clear previous gradients, compute gradients of all variables wrt loss
        optimizer.zero_grad()
        loss.backward()

        # performs updates using calculated gradients
        optimizer.step()

        # Evaluate summaries only once in a while
        if i % 10 == 0:
            # extract data from torch Variable, move to cpu, convert to numpy arrays
            output_batch = output_batch.data.cpu().numpy()
            labels_batch = labels_batch.data.cpu().numpy()

            # compute all metrics on this batch
            summary_batch = {metric: metrics[metric](output_batch, labels_batch)
                             for metric in metrics}
            summary_batch['loss'] = loss.item()
            summ.append(summary_batch)

        # update the average loss
        loss_avg.update(loss.item())
        t.set_postfix(loss='{:05.3f}'.format(loss_avg()))

    # compute mean of all metrics in summary
    metrics_mean = {metric: np.mean([x[metric]
                                     for x in summ]) for metric in summ[0]}
    metrics_string = " ; ".join("{}: {:05.3f}".format(k, v)
                                for k, v in metrics_mean.items())
    print("- Train metrics: " + metrics_string)

In [89]:
def evaluate(model, loss_fn, data_iterator, metrics, num_steps):
    """Evaluate the model on `num_steps` batches.

    Args:
        model: (torch.nn.Module) the neural network
        loss_fn: a function that takes batch_output and batch_labels and computes the loss for the batch
        data_iterator: (generator) a generator that generates batches of data and labels
        metrics: (dict) a dictionary of functions that compute a metric using the output and labels of each batch
        params: (Params) hyperparameters
        num_steps: (int) number of batches to train on, each of size params.batch_size
    """

    # set model to evaluation mode
    model.eval()

    # summary for current eval loop
    summ = []

    # compute metrics over the dataset
    for _ in range(num_steps):
        # fetch the next evaluation batch
        data_batch, labels_batch, _ = next(data_iterator)

        # compute model output
        output_batch = model(data_batch)
        loss = loss_fn(output_batch, labels_batch)

        # extract data from torch Variable, move to cpu, convert to numpy arrays
        output_batch = output_batch.data.cpu().numpy()
        labels_batch = labels_batch.data.cpu().numpy()

        # compute all metrics on this batch
        summary_batch = {metric: metrics[metric](output_batch, labels_batch)
                         for metric in metrics}
        summary_batch['loss'] = loss.item()
        summ.append(summary_batch)

    # compute mean of all metrics in summary
    print(f"summ: {summ}")
    metrics_mean = {metric:np.mean([x[metric] for x in summ]) for metric in summ[0]}
    metrics_string = " ; ".join("{}: {:05.3f}".format(k, v) for k, v in metrics_mean.items())
    print("- Eval metrics : " + metrics_string)
    return metrics_mean

In [90]:
def train_and_evaluate(
        model,
        train_sentences,
        train_labels,
        val_sentences,
        val_labels,
        num_epochs: int,
        batch_size: int,
        optimizer,
        loss_fn,
        metrics
):
    for epoch in range(num_epochs):
        # Run one epoch
        print("Epoch {}/{}".format(epoch + 1, num_epochs))

        # compute number of batches in one epoch (one full pass over the training set)
        num_steps = (len(train_sentences) + 1) // batch_size
        train_data_iterator = data_iterator(
            train_sentences, train_labels, len(train_sentences), batch_size, shuffle=True)
        train(model, optimizer, loss_fn, train_data_iterator,
              metrics, num_steps)

        # Evaluate for one epoch on validation set
        num_steps = (len(val_sentences) + 1) // batch_size
        val_data_iterator = data_iterator(
            val_sentences, val_labels, len(val_sentences), batch_size, shuffle=False)
        val_metrics = evaluate(
            model, loss_fn, val_data_iterator, metrics, num_steps)
   

In [91]:
inv_vocab = {v: k for k, v in vocab.items()}
inv_tag_map = {v: k for k, v in tag_map.items()}

def id_to_words(sentence):
    new_sentence = [inv_vocab[i] for i in sentence]
    return new_sentence

def id_to_labels(labels):
    new_sentence = [inv_tag_map[i] for i in labels]
    return new_sentence


In [92]:
def accuracy(outputs, labels):
    """
    Compute the accuracy, given the outputs and labels for all tokens. Exclude PADding terms.

    Args:
        outputs: (np.ndarray) dimension batch_size*seq_len x num_tags - log softmax output of the model
        labels: (np.ndarray) dimension batch_size x seq_len where each element is either a label in
                [0, 1, ... num_tag-1], or -1 in case it is a PADding token.

    Returns: (float) accuracy in [0,1]
    """

    # reshape labels to give a flat vector of length batch_size*seq_len
    labels = labels.ravel()

    # since PADding tokens have label -1, we can generate a mask to exclude the loss from those terms
    mask = (labels >= 0)

    # np.argmax gives us the class predicted for each token by the model
    outputs = np.argmax(outputs, axis=1)


    # compare outputs with labels and divide by number of tokens (excluding PADding tokens)
    return np.sum(outputs == labels)/float(np.sum(mask))



def calculate_multiclass_f1_score(outputs, labels):
    
    labels = labels.ravel()
    mask = (labels >= 0)  
    outputs = np.argmax(outputs, axis=1)
    outputs = outputs[mask]
    labels = labels[mask]
    outputs = id_to_labels(outputs)
    labels = id_to_labels(labels)
    outputs = np.expand_dims(outputs, axis=0)
    labels = np.expand_dims(labels, axis=0)
    outputs = outputs.tolist()
    labels = labels.tolist()
    f1= f1_score_seqeval(labels, outputs, mode='strict', scheme=IOB1)
    return f1

def classification_report_gen(outputs, labels):
    labels = labels.ravel()
    mask = (labels >= 0)  
    outputs = np.argmax(outputs, axis=1)
    outputs = outputs[mask]
    labels = labels[mask]
    outputs = id_to_labels(outputs)
    labels = id_to_labels(labels)
    outputs = np.expand_dims(outputs, axis=0)
    labels = np.expand_dims(labels, axis=0)
    outputs = outputs.tolist()
    labels = labels.tolist()
    return classification_report(labels, outputs, mode='strict', scheme=IOB1)
    
def calculate_multiclass_f1_score2(outputs, labels):
    
    labels = labels.ravel()
    mask = (labels >= 0)  
    outputs = np.argmax(outputs, axis=1)
    outputs = outputs[mask]
    labels = labels[mask]
    f1= f1_score(labels, outputs, average='macro')
    return f1

def calculate_multiclass_f1_score3(outputs, labels):
    
    labels = labels.ravel()
    mask = (labels >= 0)  
    outputs = np.argmax(outputs, axis=1)
    outputs = outputs[mask]
    labels = labels[mask]
    f1= f1_score(labels, outputs, average='micro')
    return f1


metrics = {
    'f1_seqeval': calculate_multiclass_f1_score,
    'f1_micro': calculate_multiclass_f1_score3,
    'f1 macro': calculate_multiclass_f1_score2,
    'accuracy': accuracy
    # could add more metrics such as accuracy for each token type
}

In [96]:
import warnings
warnings.filterwarnings('ignore')

In [97]:
# manually change vocab size (unique no. of words) and change label size (unique no. of labels) for now
model = Net(embedding_weights, 300, 300, len(tag_map))
optimizer = optim.Adam(model.parameters(), lr=0.001)


if (os.path.isfile("model_weights.pth")):
    model.load_state_dict(torch.load('model_weights.pth'))
else:
    train_and_evaluate(model, train_sentences, train_labels, val_sentences, val_labels, 100, 5, optimizer, loss_fn, metrics)
    torch.save(model.state_dict(), 'model_weights.pth')


Epoch 1/100


100%|██████████| 2808/2808 [00:40<00:00, 69.27it/s, loss=0.177]


- Train metrics: f1_seqeval: 0.694 ; f1_micro: 0.946 ; f1 macro: 0.765 ; accuracy: 0.946 ; loss: 0.181
summ: [{'f1_seqeval': 0.787878787878788, 'f1_micro': 0.967479674796748, 'f1 macro': 0.8057004830917874, 'accuracy': 0.967479674796748, 'loss': 0.08772121369838715}, {'f1_seqeval': 0.8484848484848485, 'f1_micro': 0.9821428571428571, 'f1 macro': 0.9146911952700544, 'accuracy': 0.9821428571428571, 'loss': 0.10817364603281021}, {'f1_seqeval': 0.896551724137931, 'f1_micro': 0.9857142857142858, 'f1 macro': 0.8476480284011665, 'accuracy': 0.9857142857142858, 'loss': 0.06848486512899399}, {'f1_seqeval': 0.7142857142857143, 'f1_micro': 0.9545454545454546, 'f1 macro': 0.6666666666666666, 'accuracy': 0.9545454545454546, 'loss': 0.22159747779369354}, {'f1_seqeval': 0.8461538461538461, 'f1_micro': 0.9611650485436893, 'f1 macro': 0.88265837585034, 'accuracy': 0.9611650485436893, 'loss': 0.15315672755241394}, {'f1_seqeval': 0.8076923076923077, 'f1_micro': 0.944954128440367, 'f1 macro': 0.55336927223

100%|██████████| 2808/2808 [00:40<00:00, 69.70it/s, loss=0.101]


- Train metrics: f1_seqeval: 0.817 ; f1_micro: 0.972 ; f1 macro: 0.866 ; accuracy: 0.972 ; loss: 0.098
summ: [{'f1_seqeval': 0.787878787878788, 'f1_micro': 0.975609756097561, 'f1 macro': 0.8573099415204679, 'accuracy': 0.975609756097561, 'loss': 0.07727505266666412}, {'f1_seqeval': 0.8484848484848485, 'f1_micro': 0.9821428571428571, 'f1 macro': 0.9146911952700544, 'accuracy': 0.9821428571428571, 'loss': 0.10661279410123825}, {'f1_seqeval': 0.896551724137931, 'f1_micro': 0.9857142857142858, 'f1 macro': 0.8476480284011665, 'accuracy': 0.9857142857142858, 'loss': 0.06975090503692627}, {'f1_seqeval': 0.7142857142857143, 'f1_micro': 0.9545454545454546, 'f1 macro': 0.6666666666666666, 'accuracy': 0.9545454545454546, 'loss': 0.18803685903549194}, {'f1_seqeval': 0.8461538461538461, 'f1_micro': 0.9611650485436893, 'f1 macro': 0.88265837585034, 'accuracy': 0.9611650485436893, 'loss': 0.12943941354751587}, {'f1_seqeval': 0.8076923076923077, 'f1_micro': 0.944954128440367, 'f1 macro': 0.55336927223

...

- Train metrics: f1_seqeval: 0.979 ; f1_micro: 0.996 ; f1 macro: 0.983 ; accuracy: 0.996 ; loss: 0.012
summ: [{'f1_seqeval': 0.8484848484848485, 'f1_micro': 0.983739837398374, 'f1 macro': 0.8911111111111112, 'accuracy': 0.983739837398374, 'loss': 0.0733356922864914}, {'f1_seqeval': 0.9090909090909091, 'f1_micro': 0.9880952380952381, 'f1 macro': 0.9670721476510067, 'accuracy': 0.9880952380952381, 'loss': 0.07710064947605133}, {'f1_seqeval': 0.9655172413793104, 'f1_micro': 0.9928571428571429, 'f1 macro': 0.9324965132496512, 'accuracy': 0.9928571428571429, 'loss': 0.14978376030921936}, {'f1_seqeval': 0.7142857142857143, 'f1_micro': 0.9545454545454546, 'f1 macro': 0.6666666666666666, 'accuracy': 0.9545454545454546, 'loss': 0.2453250288963318}, {'f1_seqeval': 0.9803921568627451, 'f1_micro': 0.9902912621359223, 'f1 macro': 0.9753042233357194, 'accuracy': 0.9902912621359223, 'loss': 0.04935256764292717}, {'f1_seqeval': 0.830188679245283, 'f1_micro': 0.944954128440367, 'f1 macro': 0.6403309209

100%|██████████| 2808/2808 [00:41<00:00, 67.75it/s, loss=0.014]


- Train metrics: f1_seqeval: 0.979 ; f1_micro: 0.997 ; f1 macro: 0.984 ; accuracy: 0.997 ; loss: 0.012
summ: [{'f1_seqeval': 0.787878787878788, 'f1_micro': 0.975609756097561, 'f1 macro': 0.8573099415204679, 'accuracy': 0.975609756097561, 'loss': 0.06679369509220123}, {'f1_seqeval': 0.9090909090909091, 'f1_micro': 0.9880952380952381, 'f1 macro': 0.9670721476510067, 'accuracy': 0.9880952380952381, 'loss': 0.11803792417049408}, {'f1_seqeval': 0.9655172413793104, 'f1_micro': 0.9928571428571429, 'f1 macro': 0.9324965132496512, 'accuracy': 0.9928571428571429, 'loss': 0.16699467599391937}, {'f1_seqeval': 0.7142857142857143, 'f1_micro': 0.9545454545454546, 'f1 macro': 0.6666666666666666, 'accuracy': 0.9545454545454546, 'loss': 0.2974821627140045}, {'f1_seqeval': 0.9411764705882353, 'f1_micro': 0.9805825242718447, 'f1 macro': 0.9613997113997114, 'accuracy': 0.9805825242718447, 'loss': 0.06453725695610046}, {'f1_seqeval': 0.830188679245283, 'f1_micro': 0.944954128440367, 'f1 macro': 0.6403309209

100%|██████████| 2808/2808 [00:41<00:00, 67.36it/s, loss=0.014]


- Train metrics: f1_seqeval: 0.979 ; f1_micro: 0.997 ; f1 macro: 0.982 ; accuracy: 0.997 ; loss: 0.012
summ: [{'f1_seqeval': 0.8484848484848485, 'f1_micro': 0.983739837398374, 'f1 macro': 0.8911111111111112, 'accuracy': 0.983739837398374, 'loss': 0.07184327393770218}, {'f1_seqeval': 0.9090909090909091, 'f1_micro': 0.9880952380952381, 'f1 macro': 0.9670721476510067, 'accuracy': 0.9880952380952381, 'loss': 0.11675726622343063}, {'f1_seqeval': 0.9655172413793104, 'f1_micro': 0.9928571428571429, 'f1 macro': 0.9324965132496512, 'accuracy': 0.9928571428571429, 'loss': 0.1713857352733612}, {'f1_seqeval': 0.7142857142857143, 'f1_micro': 0.9545454545454546, 'f1 macro': 0.6666666666666666, 'accuracy': 0.9545454545454546, 'loss': 0.2280999720096588}, {'f1_seqeval': 0.9803921568627451, 'f1_micro': 0.9902912621359223, 'f1 macro': 0.9753042233357194, 'accuracy': 0.9902912621359223, 'loss': 0.052115075290203094}, {'f1_seqeval': 0.830188679245283, 'f1_micro': 0.944954128440367, 'f1 macro': 0.640330920

In [98]:
'''Test batch- tensor of n_sentences x max_len_sentence
   Labels_batch- tensor of n_sentences x max_len_sentence
   Test sentences- list of n_sentences x sentence_length(no padding)'''
print(len(test_sentences))
test_data_iterator = data_iterator(test_sentences, test_labels, len(test_sentences), len(test_sentences), shuffle=True)
test_batch, labels_batch, test_sentences = next(test_data_iterator)



3453


In [99]:
print(f"type test: {type(test_batch)}")
print(f"len test: {len(test_batch)}")
print(f"type label: {type(labels_batch)}")
print(f"len label: {len(labels_batch)}")

type test: <class 'torch.Tensor'>
len test: 3453
type label: <class 'torch.Tensor'>
len label: 3453


In [100]:
model_output = model(test_batch)

In [101]:
model_output_numpy = model_output.detach().numpy()
labels_batch_numpy = labels_batch.detach().numpy()

In [102]:
f1_score_seqeval = calculate_multiclass_f1_score(model_output_numpy, labels_batch_numpy)
f1_score_macro = calculate_multiclass_f1_score2(model_output_numpy, labels_batch_numpy)
f1_score_micro = calculate_multiclass_f1_score3(model_output_numpy, labels_batch_numpy)

In [103]:
print(f"f1_score_seqeval: {f1_score_seqeval}")
print(f"f1_score_macro: {f1_score_macro}")
print(f"f1_score_micro: {f1_score_micro}")

f1_score_seqeval: 0.7688017429193901
f1_score_macro: 0.5286832204172486
f1_score_micro: 0.9611715300958329


In [104]:

model_class_report = classification_report_gen(model_output_numpy, labels_batch_numpy)
print(f"model_class_report: \n{model_class_report}")

model_class_report: 
              precision    recall  f1-score   support

         LOC       0.80      0.86      0.83      1661
        MISC       0.64      0.64      0.64       702
         ORG       0.68      0.72      0.70      1655
         PER       0.84      0.84      0.84      1611

   micro avg       0.75      0.78      0.77      5629
   macro avg       0.74      0.76      0.75      5629
weighted avg       0.76      0.78      0.77      5629



In [ ]:
predicted_labels = np.argmax(model_output.detach().numpy(), axis=1)
print(f"sentences_w_words \n {len(test_sentences)}")
print(f"predicted_labels \n {len(predicted_labels)}")

sentences_w_words 
 3453
predicted_labels 
 428172


In [ ]:
sample_output = model(test_batch[10].unsqueeze(0))
id_to_words(test_sentences[10])


['Yevgeny',
 'Kafelnikov',
 'UNK',
 'Russia',
 'UNK',
 'beat',
 'Jim',
 'Courier',
 'UNK',
 'U.S.',
 'UNK',
 'UNK',
 'UNK',
 'UNK']

In [ ]:
sample_mask = (labels_batch[10] >= 0)
sample_label_predict = np.argmax(sample_output.detach().numpy(), axis=1)[sample_mask]
sample_label_true = labels_batch[10][sample_mask]

In [ ]:
print(f"sample_label_predict: {id_to_labels(sample_label_predict)}")
print(f"sample_label_true: {id_to_labels(sample_label_true.numpy())}")

sample_label_predict: ['I-PER', 'I-PER', 'O', 'I-LOC', 'O', 'O', 'I-PER', 'I-PER', 'O', 'I-LOC', 'O', 'O', 'O', 'O']
sample_label_true: ['I-PER', 'I-PER', 'O', 'I-LOC', 'O', 'O', 'I-PER', 'I-PER', 'O', 'I-LOC', 'O', 'O', 'O', 'O']
